In [1]:
import plotly.plotly as py
import pandas as pd
import numpy as np
import re
from tqdm import tqdm_notebook as tqdm

In [3]:
# You will need this file specified 
# Load the data
# data located at https://drive.google.com/open?id=1Lp5N2vNMYqoPMQkCOExjS6CWCwWg3PSq
# please put in valid folder 
df = pd.read_csv("../Twitter_to_vec/mass_sentiment_data.csv")

In [3]:
# Take a look at the data
df.head()

Unnamed: 0        id_str  \
0           0  9.864028e+17   
1           1  9.874308e+17   
2           2  9.855298e+17   
3           3  9.815095e+17   
4           4  9.870842e+17   

                                                text  \
0  Poor Ralph! He wants to save the team and not ...   
1  Another great day of bread baking @bufoodandwi...   
2  “THIS IS OUR FUCKIN CITY” -Big Papi #OneBoston...   
3  “You may write me down in history\nWith your b...   
4  Automating release deployments across multiple...   

                                         coordinates  favorite_count  \
0                                                NaN             0.0   
1  {'type': 'Point', 'coordinates': [-71.0565, 42...             0.0   
2                                                NaN             0.0   
3                                                NaN             0.0   
4                                                NaN             0.0   

                                                user  \
0  {'profile_background_color': '0A0808', 'create...   
1  {'profile_background_color': 'EDECE9', 'create...   
2  {'profile_background_color': 'C0DEED', 'create...   
3  {'profile_background_color': 'C0DEED', 'create...   
4  {'profile_background_color': 'C0DEED', 'create...   

                                            entities  \
0  {'hashtags': [{'indices': [56, 65], 'text': 'T...   
1  {'hashtags': [{'indices': [56, 74], 'text': 'b...   
2  {'hashtags': [{'indices': [36, 49], 'text': 'O...   
3  {'hashtags': [], 'urls': [{'url': 'https://t.c...   
4  {'hashtags': [], 'urls': [{'url': 'https://t.c...   

                                hashtags  preds  w_preds  pos_proba  \
0                           ['TheFlash']      0      0.0   0.019119   
1  ['breadmakesthemeal', 'artisanbread']      0      0.0   0.469331   
2       ['OneBostonDay', 'BostonStrong']      0      0.0   0.449416   
3                                     []      1      0.0   0.732388   
4                                     []      1      0.0   0.937351   

   w_pos_proba  
0          0.0  
1          0.0  
2          0.0  
3          0.0  
4          0.0

In [4]:
coord_df = df.loc[df['coordinates'].notnull()]

In [5]:
coord_df = coord_df.loc[coord_df.text.notnull()]

In [6]:
#[longitude, latitude].
coord_df.coordinates
lat = []
long = []
for i in coord_df.coordinates.values:
    i=eval(i)
    lat += [i['coordinates'][1] ]
    long += [i['coordinates'][0] ]

In [7]:
del df # save memory 

In [8]:
coord_df['lat']=lat
coord_df['long']=long

In [9]:
full_coord = coord_df
full_coord= full_coord.sort_values('pos_proba', ascending=False).reset_index()

In [14]:
# this will have the most positive and most negative tweets to view 
coord_df = full_coord.iloc[:2000 ]
coord_df= coord_df.append(full_coord.iloc[-2001:-1 ])
coord_df.shape

(4000, 15)

In [15]:
coord_df.head()

index  Unnamed: 0        id_str  \
0   43410       43410  9.845853e+17   
1  198087      198087  9.873232e+17   
2  281672      281672  9.896819e+17   
3   58805       58805  9.813212e+17   
4  111004      111004  9.900529e+17   

                                                text  \
0                           @findmyway37 I’m glad :)   
1                               Happy #godofwar day!   
2                                  @aphoenix Thanks!   
3  Obsessed with my new Meinl 14” Byzance Traditi...   
4  Woohoo! When Austin Street tells you you shoul...   

                                         coordinates  favorite_count  \
0  {'type': 'Point', 'coordinates': [-71.05952379...             0.0   
1  {'type': 'Point', 'coordinates': [-71.200927, ...             0.0   
2  {'type': 'Point', 'coordinates': [-71.00205994...             0.0   
3  {'type': 'Point', 'coordinates': [-71.087258, ...             0.0   
4  {'type': 'Point', 'coordinates': [-70.8991, 42...             0.0   

                                                user  \
0  {'profile_background_color': '022330', 'create...   
1  {'profile_background_color': 'C0DEED', 'create...   
2  {'profile_background_color': '3C3C3C', 'create...   
3  {'profile_background_color': '1A1B1F', 'create...   
4  {'profile_background_color': 'C0DEED', 'create...   

                                            entities       hashtags  preds  \
0  {'hashtags': [], 'urls': [], 'symbols': [], 'u...             []      1   
1  {'hashtags': [{'indices': [6, 15], 'text': 'go...   ['godofwar']      1   
2  {'hashtags': [], 'urls': [], 'symbols': [], 'u...             []      1   
3  {'hashtags': [], 'urls': [{'url': 'https://t.c...             []      1   
4  {'hashtags': [{'indices': [102, 112], 'text': ...  ['beergreat']      1   

   w_preds  pos_proba  w_pos_proba        lat       long  
0      0.0   0.999112          0.0  42.359592 -71.059524  
1      0.0   0.998535          0.0  42.294375 -71.200927  
2      0.0   0.996085          0.0  42.373123 -71.002060  
3      0.0   0.993095          0.0  42.346988 -71.087258  
4      0.0   0.990666          0.0  42.750600 -70.899100

In [16]:
import plotly.offline as py
import pandas as pd
# Make plotly work with Jupyter notebook
py.init_notebook_mode()

In [17]:
# Define colors 
scl = [ [0,"rgb(5, 10, 172)"],[0.35,"rgb(40, 60, 190)"],[0.5,"rgb(70, 100, 245)"],\
    [0.6,"rgb(90, 120, 245)"],[0.7,"rgb(106, 137, 247)"],[1,"rgb(220, 220, 220)"] ]

sc2 = [[0.0, 'rgb(165,0,38)'], [0.1111111111111111, 'rgb(215,48,39)'], [0.2222222222222222, 'rgb(244,109,67)'], [0.3333333333333333, 'rgb(253,174,97)'], [0.4444444444444444, 'rgb(254,224,144)'], [0.5555555555555556, 'rgb(224,243,248)'], [0.6666666666666666, 'rgb(171,217,233)'], [0.7777777777777778, 'rgb(116,173,209)'], [0.8888888888888888, 'rgb(69,117,180)'], [1.0, 'rgb(49,54,149)']]
sc3=[[0.0, 'rgb(165,0,38)'], [0.1111111111111111, 'rgb(215,48,39)'], [0.2222222222222222, 'rgb(244,109,67)'],
        [0.3333333333333333, 'rgb(253,174,97)'], [0.4444444444444444, 'rgb(254,224,144)'], [0.5555555555555556, 'rgb(224,243,248)'],
        [0.6666666666666666, 'rgb(171,217,233)'],[0.7777777777777778, 'rgb(116,173,209)'], [0.8888888888888888, 'rgb(69,117,180)'],
        [1.0, 'rgb(49,54,149)']]

In [18]:
data = [ dict(
        #type = 'scattergeo',
        #locationmode = 'USA-states',
        lon = coord_df['long'],
        lat = coord_df['lat'],
        text = coord_df['text'],
        marker = dict(
            color = coord_df['pos_proba'],
            colorscale = sc3,
            #reversescale = True,
            symbol = 'diamond',
            opacity = 0.5,
            size = 4,
            colorbar = dict(
                thickness = 10,
                titleside = "right",
                outlinecolor = "rgba(68, 68, 68, 0)",
                ticks = "outside",
                ticklen = 3,
                showticksuffix = "last",
                ticksuffix = " Sentiment",
                dtick = 0.1
            ),
        ),
        type = 'scattergeo'
    ) ]
    
 

In [19]:
layout = dict(
    geo = dict(
        scope = ['usa'],
        locationmode = 'USA-states',
        showland = True,
        landcolor = "rgb(212, 212, 212)",
        subunitcolor = "rgb(255, 255, 255)",
        countrycolor = "rgb(255, 255, 255)",
        showsubunits = True,
        showcountries = True,
        show_state_data=True,
        showrivers=True,
        plot_bgcolor='rgb(229,229,229)',
        paper_bgcolor='rgb(229,229,229)',
        show_hover=True,
        resolution = 50,
        width=1300,
        height=750,
        #county_outline={'color': 'rgb(255,255,255)', 'width': 0.5},
    exponent_format=True,
         projection=dict( type='albers usa' , scale=0.7290046894082897),
       
        #[latitude_start, longitude_start, latitude_finish, longitude_finish]
        #-71.1912, 42.2279, -70.8085, 42.3973)
        #-73.5081,41.1871,-69.8589,42.8868
        lonaxis = dict(
            showgrid = True,
            gridwidth = 0.5,
            width=1000,
            height=500,
            range= [-73,-69.8589 ],
            dtick = 5
        ),
        lataxis = dict (
            showgrid = True,
            gridwidth = 0.5,
            range= [41, 43],
            dtick = 5
        ),
        center = dict(lon=-71.9541948881738 , lat=42.40035335350683),
    ),
    title = 'Twitter Sentiment Analysis',
)

In [20]:
fig = { 'data':data, 'layout':layout }
#dict( data=data, layout=layout )
py.iplot( fig, validate=False, filename='twitter_plot' )

In [21]:
pos = coord_df.pos_proba
neg = 1-pos
s = pos + neg
pos = np.sum(pos) / np.sum(s)
neg = np.sum(neg)/ np.sum(s)
c = ['#6495ED', '#DC143C']
data1, labels1 = [ pos, neg], ["+ pred", '- pred']

In [22]:
preds = coord_df.preds
pos_preds = preds.sum() / len(preds)
neg_preds = 1- pos_preds
data2, labels2 = [pos_preds, neg_preds], ['+ predict', '- predict']

In [24]:
from bqplot import *
from ipywidgets import interactive, fixed, IntSlider, HTML, HTMLMath, FloatSlider,HBox, Button

pie1 = Pie(sizes=data1, radius=180, sort=False, 
          display_labels='outside', display_values=True,
          values_format='.0%', labels=labels1,colors=c)
pie2= Pie(sizes=data2, radius=180, sort=False, 
          display_labels='outside', display_values=True,
          values_format='.0%', labels=labels2,colors=c)

HBox( (Figure(marks=[pie1], animation_duration=1000), Figure(marks=[pie2], animation_duration=1000)))

In [25]:
pie1.sort = True
with pie1.hold_sync():
    pie1.radius = 180
    pie1.inner_radius = 120
pie2.sort = True
with pie2.hold_sync():
    pie2.radius = 180
    pie2.inner_radius = 120

In [26]:
def hash_tag_sent_build(df):
    hashtags = {}
    hts = df.hashtags.values
    pos_proba = df.pos_proba.values
    for i in tqdm(range(len(hts))):
        tmp_tag = list(eval(hts[i]))
        if len(tmp_tag) > 0:
            for j in tmp_tag:
                if j not in hashtags:
                    hashtags[j] = {0:0, 1:1, 'Count':0}
                hashtags[j][0] += (1- pos_proba[i])
                hashtags[j][1] += pos_proba[i]
                hashtags[j]['Count']+=1
    ret_df =  pd.DataFrame.from_dict(hashtags, orient='index').sort_values("Count", ascending=False)
    ret_df['pos'] = ret_df[1]/ ret_df['Count']
    ret_df['neg'] = ret_df[0]/ret_df["Count"]
    return ret_df.loc[ret_df["Count"] > 1]

In [27]:
ht_df = hash_tag_sent_build(coord_df)
#ht_df.sort_values("Count", ascending=False)
ht_df

0           1  Count       pos       neg
Job                 624.460294  136.539706    760  0.179658  0.821658
Jobs                624.460294  136.539706    760  0.179658  0.821658
Hiring              622.107825  134.892175    756  0.178429  0.822894
CareerArc           607.697699  132.302301    739  0.179029  0.822324
Boston              353.330206   86.669794    439  0.197425  0.804852
IT                   53.961916   13.038084     66  0.197547  0.817605
DellJobs             45.868396   12.131604     57  0.212835  0.804709
boston               11.852309   41.147691     52  0.791302  0.227929
Cambridge            33.329806    9.670194     42  0.230243  0.793567
photo                 7.405074   33.594926     40  0.839873  0.185127
BOS                  33.670565    4.329435     37  0.117012  0.910015
Construction         29.724505    7.275495     36  0.202097  0.825681
bizdev               29.111856    6.888144     35  0.196804  0.831767
flightdelay          31.240946    3.759054     34  0.110560  0.918851
Sales                26.565955    7.434045     33  0.225274  0.805029
bostonmarathon        9.272630   23.727370     32  0.741480  0.289770
hiring               23.078509    7.921491     30  0.264050  0.769284
Veterans             25.627713    4.372287     29  0.150769  0.883714
paxeast2018          10.139563   16.860437     26  0.648478  0.389983
dorchester           20.480428    5.519572     25  0.220783  0.819217
ProjectMgmt          20.333946    5.666054     25  0.226642  0.813358
Engineering          19.760595    5.239405     24  0.218309  0.823358
OralSurgery          18.525437    5.474563     23  0.238024  0.805454
BusinessMgmt         17.945356    5.054644     22  0.229757  0.815698
Nursing              16.544152    4.455848     20  0.222792  0.827208
Banking              16.691976    4.308024     20  0.215401  0.834599
RealEstate           16.583946    4.416054     20  0.220803  0.829197
Actuarial            16.591523    4.408477     20  0.220424  0.829576
Retail               16.381942    4.618058     20  0.230903  0.819097
InvestmentBanking    16.460052    4.539948     20  0.226997  0.823003
...                        ...         ...    ...       ...       ...
zntarts               0.984462    2.015538      2  1.007769  0.492231
nyc                   0.171816    2.828184      2  1.414092  0.085908
bourbon               0.173998    2.826002      2  1.413001  0.086999
najaamlee             0.128265    2.871735      2  1.435867  0.064133
sunday                0.106838    2.893162      2  1.446581  0.053419
hairstyle             0.141041    2.858959      2  1.429480  0.070520
WizRaptors            0.190713    2.809287      2  1.404644  0.095356
Facebook              0.157307    2.842693      2  1.421346  0.078654
nationalsiblingday    0.169587    2.830413      2  1.415206  0.084794
barbrastreisand       0.075504    2.924496      2  1.462248  0.037752
fenway                0.142528    2.857472      2  1.428736  0.071264
goodnight             0.209105    2.790895      2  1.395447  0.104553
bostonbruins          1.799896    1.200104      2  0.600052  0.899948
good                  0.123863    2.876137      2  1.438069  0.061931
italian               0.996772    2.003228      2  1.001614  0.498386
ymca                  0.186056    2.813944      2  1.406972  0.093028
Driver                1.671365    1.328635      2  0.664318  0.835682
onrepeat              0.107483    2.892517      2  1.446259  0.053741
allston               0.143376    2.856624      2  1.428312  0.071688
happyfriday           0.186765    2.813235      2  1.406618  0.093382
goodmorning           0.201573    2.798427      2  1.399214  0.100786
finisher              0.130887    2.869113      2  1.434557  0.065443
fbf                   0.150260    2.849740      2  1.424870  0.075130
goodwillfinds         0.083356    2.916644      2  1.458322  0.041678
gopenskecareers       1.634319    1.365681      2  0.682841  0.817159
bostonglobe           0.148690    2.851

In [28]:
xs = OrdinalScale()
ys = LinearScale()

bar = Bars(x=ht_df.index.values[:15], y=ht_df.pos.values[:15], scales={'x': xs, 'y': ys}, padding=0.2, type='grouped')
xax = Axis(scale=xs)
yax = Axis(scale=ys, orientation='vertical', tick_format='0.0%', grid_lines='solid')
fig = Figure(marks=[bar], axes=[xax, yax], animation_duration=1000, )
fig.layout.width = '1000px'
fig

Figure(animation_duration=1000, axes=[Axis(scale=OrdinalScale()), Axis(orientation='vertical', scale=LinearSca…

In [36]:
tok = eval(open('../../auth.json').read())["mapbox_access_token"]

In [39]:
from plotly.graph_objs import *
# mapbox_access_token = 'ADD_YOUR_TOKEN_HERE'

data = Data([
    Scattermapbox(
        lat=coord_df.lat,
        lon=coord_df.long,
        mode='markers',
        text = coord_df['text'],
        marker=Marker(
            color = coord_df['pos_proba'],
            colorscale = sc3,
            reversescale = False,
            opacity=.3,
            size = 5,
            colorbar = dict(
                thickness = 10,
                titleside = "right",
                outlinecolor = "rgba(68, 68, 68, 0)",
                ticks = "outside",
                showticksuffix = "last",
                ticksuffix = " Sentiment",
                dtick = 0.1
            ),
        ),
        #text=['Montreal'],
    )
])

layout = Layout(
    autosize=False,
    width=800,
    height=800,
    hovermode='closest',
    mapbox=dict(
        accesstoken=tok,
        bearing=0,
        center=dict(
        lon=-71.0541948881738 , lat=42.36035335350683) ,
        pitch=0,
        zoom=10
    ),
)

fig = dict(data=data, layout=layout)
py.iplot(fig, filename='Montreal Mapbox')